In [1]:
SCOPETYPE = 'OPENADC'
PLATFORM = 'CW308_STM32F4'
CRYPTO_TARGET = 'TINYAES128C'
SS_VER='SS_VER_2_1'

In [2]:
%run "../../Setup_Scripts/Setup_Generic.ipynb"

INFO: Found ChipWhisperer😍


In [3]:
#定義執行sh命令的函數
from IPython import get_ipython

def run_bash_command(command):
    shell = get_ipython()
    result = shell.run_cell_magic('sh','', command)
# run_bash_command('cd ..;ls')


# run_bash_command('make PLATFORM="CW308_STM32F4" CRYPTO_TARGET="TINYAES128C" SS_VER="SS_VER_2_1"')

In [4]:
def my_complier1():
    run_bash_command('cd ../../../hardware/victims/firmware/pqm4_L2;make PLATFORM=CW308_STM32F4 CRYPTO_TARGET=TINYAES128C SS_VER=SS_VER_2_1')
    return True
if my_complier1():
    print("編譯成功")

Building for platform CW308_STM32F4 with CRYPTO_TARGET=TINYAES128C
SS_VER set to SS_VER_2_1
SS_VER set to SS_VER_2_1
Blank crypto options, building for AES128
Building for platform CW308_STM32F4 with CRYPTO_TARGET=TINYAES128C
SS_VER set to SS_VER_2_1
SS_VER set to SS_VER_2_1
Blank crypto options, building for AES128
make[1]: '.dep' is up to date.
Building for platform CW308_STM32F4 with CRYPTO_TARGET=TINYAES128C
SS_VER set to SS_VER_2_1
SS_VER set to SS_VER_2_1
Blank crypto options, building for AES128
.
Welcome to another exciting ChipWhisperer target build!!
arm-none-eabi-gcc (GNU Arm Embedded Toolchain 10-2020-q4-major) 10.2.1 20201103 (release)
Copyright (C) 2020 Free Software Foundation, Inc.
This is free software; see the source for copying conditions.  There is NO
warranty; not even for MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.

.
Compiling:


PQCgenKAT_sign.c: In function 'dilithium1':
PQCgenKAT_sign.c:256:9: warning: 'm' is used uninitialized in this function [-Wuninitialized]
  256 |         free(m);
      |         ^~~~~~~


    PQCgenKAT_sign.c ...Done!
.
Compiling:
    sign.c ...Done!
.
Compiling:
    packing.c ...Done!
.
Compiling:
    poly.c ...Done!
.
Compiling:
    polyvec.c ...Done!
.
Compiling:
    rounding.c ...Done!
.
Compiling:
    symmetric-shake.c ...Done!
.
Compiling:
    smallpoly.c ...Done!
.
Compiling:
    fips202.c ...Done!
.
Compiling:
    .././simpleserial/simpleserial.c ...Done!
.
Compiling:


In file included from .././hal/stm32f4/stm32f4_hal.c:3:
.././hal/stm32f4/stm32f4_hal_lowlevel.h:108: warning: "STM32F415xx" redefined
  108 | #define STM32F415xx
      | 
<command-line>: note: this is the location of the previous definition


    .././hal/stm32f4/stm32f4_hal.c ...Done!
.
Compiling:


In file included from .././hal/stm32f4/stm32f4_hal_lowlevel.c:39:
.././hal/stm32f4/stm32f4_hal_lowlevel.h:108: warning: "STM32F415xx" redefined
  108 | #define STM32F415xx
      | 
<command-line>: note: this is the location of the previous definition


    .././hal/stm32f4/stm32f4_hal_lowlevel.c ...Done!
.
Compiling:
    .././hal/stm32f4/stm32f4_sysmem.c ...Done!
.
Compiling:
    .././hal/stm32f4/stm32f4xx_hal_rng.c ...Done!
.
Compiling:
    .././crypto/tiny-AES128-C/aes.c ...Done!
.
Compiling:
    .././crypto/aes-independant.c ...Done!
.
Assembling: basemul_257.S
arm-none-eabi-gcc -c -mcpu=cortex-m4 -I. -x assembler-with-cpp -mthumb -mfloat-abi=hard -mfpu=fpv4-sp-d16 -fmessage-length=0 -ffunction-sections -DF_CPU=7372800 -Wa,-gstabs,-adhlns=objdir-CW308_STM32F4/basemul_257.lst -I.././simpleserial/ -I.././simpleserial/ -I.././hal -I.././hal/stm32f4 -I.././hal/stm32f4/CMSIS -I.././hal/stm32f4/CMSIS/core -I.././hal/stm32f4/CMSIS/device -I.././hal/stm32f4/Legacy -I.././crypto/ -I.././crypto/tiny-AES128-C basemul_257.S -o objdir-CW308_STM32F4/basemul_257.o
.
Assembling: fnt_257.S
arm-none-eabi-gcc -c -mcpu=cortex-m4 -I. -x assembler-with-cpp -mthumb -mfloat-abi=hard -mfpu=fpv4-sp-d16 -fmessage-length=0 -ffunction-sections -DF_CPU=7372800

In [5]:
#maskmain-CW308_STM32F4.hex
def upload1():
    fw_path = "../../../hardware/victims/firmware/pqm4_L2/PQCgenKAT_sign-{}.hex".format(PLATFORM)
    cw.program_target(scope, prog, fw_path)
    if SS_VER == 'SS_VER_2_1':
        target.reset_comms()
    else:
        cw.program_target(scope, prog, fw_path)
    return True

if upload1():
    print("上傳成功！！！")

Detected known STMF32: STM32F40xxx/41xxx
Extended erase (0x44), this can take ten seconds or more
Attempting to program 22983 bytes at 0x8000000
STM32F Programming flash...
STM32F Reading flash...
Verified flash OK, 22983 bytes
上傳成功！！！


In [6]:
# 定义刷新函数
if SS_VER == 'SS_VER_2_1':
    if PLATFORM == "CWLITEXMEGA":
        def reboot_flush():            
            scope.io.pdic = False
            time.sleep(0.1)
            scope.io.pdic = "high_z"
            time.sleep(0.1)
            #Flush garbage too
            target.flush()
        print("xmega")
    else:
        def reboot_flush():            
            scope.io.nrst = False
            time.sleep(0.05)
            scope.io.nrst = "high_z"
            time.sleep(0.05)
            #Flush garbage too
            target.flush()
else:
    def reboot_flush():
        time.sleep(0.2)
        target.flush()

In [7]:
#随机生成消息
def get_random_message():
    import random
    choice_list = ['0','1','2','3','4','5','6','7','8','9','A','B','C','D','E','F']
    random_message = ''
    
    for i in range(66):
        random_message += random.choice(choice_list)
    
    # print('random_message is ',random_message)
    #在没有故障的情况下发送消息给硬件设备，让硬件设备运行的DiLithium算法进行签名
    # print('random_message + seed_message is ',random_message+seed_message)
    return random_message

get_random_message()    

'244D83BB201454D247AFFBFD494959A07C2A5276EA182AC0630C9A147FC84EE1C2'

In [8]:
#无故障的情况下观察ρ的值
reboot_flush()
mess = get_random_message()

p = bytearray(mess,encoding='utf-8')
target.simpleserial_write('3', p)
time.sleep(0.05)
    
output = target.simpleserial_read_witherrors('r',180)
    # p_list = []
    # for i in range(180):
    #     p_list.append(output['payload'][i])
    # print(p_list[0])
    # print(p_list[64])
    # print(p_list[128])
    # r_list = get_rhoprime(p_list)
    # print(r_list)
print(output['payload'])
p_list = []
for ii in range(20,68):
    p_list.append(output['payload'][ii])
# rhoprime_list.append(p_list)
print(p_list)


CWbytearray(b'00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 b6 60 fb db cd fa 84 b7 88 b3 83 f0 fd c6 4b 72 b7 35 f4 7c 76 78 be e3 77 81 93 cb db f7 bf dd 69 12 00 81 9f 94 f2 0a 17 ab 36 fd 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00')
[182, 96, 251, 219, 205, 250, 132, 183, 136, 179, 131, 240, 253, 198, 75, 114, 183, 53, 244, 124, 118, 120, 190, 227, 119, 129, 147, 203, 219, 247, 191, 221, 105, 18, 0, 129, 159, 148, 242, 10, 23, 171, 54, 253, 0, 0, 0, 0]


In [9]:
#无故障的情况下观察ρ的值
reboot_flush()
mess = get_random_message()

p = bytearray(mess,encoding='utf-8')
target.simpleserial_write('3', p)
time.sleep(0.05)
    
output = target.simpleserial_read_witherrors('r',180)
    # p_list = []
    # for i in range(180):
    #     p_list.append(output['payload'][i])
    # print(p_list[0])
    # print(p_list[64])
    # print(p_list[128])
    # r_list = get_rhoprime(p_list)
    # print(r_list)
print(output['payload'])
p_list = []
for ii in range(20,68):
    p_list.append(output['payload'][ii])
# rhoprime_list.append(p_list)
print(p_list)

CWbytearray(b'00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 0b 6f aa 60 de 5b 3f e2 d9 bb 7c cc 1f e5 5a 9a c8 ea cc b5 69 cd c2 4a 56 78 4c f5 d1 d8 6d eb 37 ea 3a 5d a8 2c 77 3d f9 31 79 25 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00')
[11, 111, 170, 96, 222, 91, 63, 226, 217, 187, 124, 204, 31, 229, 90, 154, 200, 234, 204, 181, 105, 205, 194, 74, 86, 120, 76, 245, 209, 216, 109, 235, 55, 234, 58, 93, 168, 44, 119, 61, 249, 49, 121, 37, 0, 0, 0, 0]


In [10]:
def test_suc(rhoprime_list):
    small_list1 = [93,198,244,83,23]
    small_list2 = [12,152,223,81,136]
    small_list3 = [236,223,30,28,59]
    small_list4 = [132,111,139,164,143]
    small_list5 =[219, 73, 236, 225, 226]
    small_list6 =[15, 180, 208, 232, 145]
    small_list7 =[213, 242, 25, 12, 177]
    small_list8 =[169, 113, 171, 29, 174]
    small_list9 =[129, 212, 47, 3, 50]
    small_list10 =[15, 119, 95, 5, 89]
    small_list11 =[250, 199, 148, 130, 124]
    small_list12 =[156, 134, 51, 137, 102]
    small_list13 =[71, 235, 134, 248, 5]
    small_list14 =[136, 22, 180, 173, 66]
    small_list15 =[160, 132, 250, 57, 138]
    small_list16 =[134, 41, 60, 198, 34]
    small_list17 =[244, 108, 53, 139, 106]
    small_list18 =[80, 115, 188, 198, 5]
    small_list19 =[95, 241, 222, 43, 40]
    small_list20 =[7, 67, 154, 200, 59]
    small_list21 =[242, 137, 18, 174, 214]
    small_list22 =[81, 219, 2, 129, 227]
    small_list23 =[83, 153, 148, 86, 84]
    small_list24 =[118, 72, 219, 201, 147]
    small_list25 =[16, 133, 226, 124, 114]
    small_list26 =[161, 231, 115, 174, 109]
    small_list27 =[225, 78, 37, 128, 241]
    small_list28 =[205, 77, 86, 3, 132]
    small_list29 =[96, 146, 102, 160, 165]
    small_list30 =[172, 225, 102, 173, 218]
    small_list31 =[128, 8, 58, 205, 226]
    small_list32 = [112,69,231,88,211]

    if rhoprime_list[:5] == small_list1:
        print('success!!!')
        print(rhoprime_list)
        return 1

    if rhoprime_list[:5] == small_list2:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list3:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list4:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list5:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list6:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list7:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list8:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list9:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list10:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list11:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list12:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list13:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list14:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list15:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list16:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list17:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list18:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list19:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list20:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list21:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list22:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list23:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list24:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list25:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list26:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list27:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list28:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list29:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list30:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list31:
        print('success!!!')
        print(rhoprime_list)
        return 1
    if rhoprime_list[:5] == small_list32:
        print('success!!!')
        print(rhoprime_list)
        return 1
    

    return 0 

test_suc([112,69,231,88,0])

0

In [11]:
#test param i < 1(for循环执行1次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 293
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(293,294)


#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate1 = success_num / 1000
print('when for execute one time ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 293
repeat      = 1
output      = clock_xor

success!!!
[93, 198, 244, 83, 23, 131, 173, 134, 78, 75, 166, 16, 42, 29, 51, 100, 166, 131, 35, 62, 110, 38, 76, 203, 186, 187, 107, 1, 188, 72, 64, 43, 122, 37, 165, 103, 5, 31, 43, 201, 233, 94, 62, 218, 0, 0, 0, 0]
success!!!
[93, 198, 244, 83, 23, 131, 173, 134, 78, 75, 166, 16, 42, 29, 51, 100, 166, 131, 35, 62, 110, 38, 76, 203, 186, 187, 107, 1, 188, 72, 64, 43, 122, 37, 165, 103, 5, 31, 43, 201, 233, 94, 62, 218, 0, 0, 0, 0]
success!!!
[93, 198, 244, 83, 23, 131, 173, 134, 78, 75, 166, 16, 42, 29, 51, 100, 166, 131, 35, 62, 110, 38, 76, 203, 186, 187, 107, 1, 188, 72, 64, 43, 122, 37, 165, 103, 5, 31, 43, 201, 233, 94, 62, 218, 0, 0, 0, 0]
success!!!
[93, 198, 244, 83, 23, 131, 173, 134, 78, 75, 166, 16, 42, 29, 51, 100, 166, 131, 35, 62, 110, 38, 76, 203, 186, 187, 107, 

In [12]:
#test param i < 2(for循环执行2次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 320
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(320,321)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate2 = success_num / 1000
print('when for execute two times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 320
repeat      = 1
output      = clock_xor

success!!!
[12, 152, 223, 81, 136, 1, 3, 212, 78, 140, 155, 7, 76, 94, 141, 134, 6, 16, 48, 122, 241, 43, 176, 9, 172, 249, 243, 255, 101, 178, 211, 115, 16, 205, 216, 130, 6, 89, 27, 218, 179, 56, 131, 221, 0, 0, 0, 0]
success!!!
[12, 152, 223, 81, 136, 1, 3, 212, 78, 140, 155, 7, 76, 94, 141, 134, 6, 16, 48, 122, 241, 43, 176, 9, 172, 249, 243, 255, 101, 178, 211, 115, 16, 205, 216, 130, 6, 89, 27, 218, 179, 56, 131, 221, 0, 0, 0, 0]
success!!!
[12, 152, 223, 81, 136, 1, 3, 212, 78, 140, 155, 7, 76, 94, 141, 134, 6, 16, 48, 122, 241, 43, 176, 9, 172, 249, 243, 255, 101, 178, 211, 115, 16, 205, 216, 130, 6, 89, 27, 218, 179, 56, 131, 221, 0, 0, 0, 0]
success!!!
[12, 152, 223, 81, 136, 1, 3, 212, 78, 140, 155, 7, 76, 94, 141, 134, 6, 16, 48, 122, 241, 43, 176, 9, 172, 249, 243, 25

In [13]:
#test param i < 3(for循环执行3次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 347
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(347,348)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate3 = success_num / 1000
print('when for execute 3 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 347
repeat      = 1
output      = clock_xor

success!!!
[236, 223, 30, 28, 59, 174, 47, 155, 227, 255, 92, 167, 52, 114, 229, 168, 243, 109, 146, 148, 142, 194, 55, 194, 147, 164, 211, 148, 26, 147, 184, 61, 91, 214, 178, 89, 51, 52, 126, 70, 221, 227, 50, 86, 0, 0, 0, 0]
success!!!
[236, 223, 30, 28, 59, 174, 47, 155, 227, 255, 92, 167, 52, 114, 229, 168, 243, 109, 146, 148, 142, 194, 55, 194, 147, 164, 211, 148, 26, 147, 184, 61, 91, 214, 178, 89, 51, 52, 126, 70, 221, 227, 50, 86, 0, 0, 0, 0]
success!!!
[236, 223, 30, 28, 59, 174, 47, 155, 227, 255, 92, 167, 52, 114, 229, 168, 243, 109, 146, 148, 142, 194, 55, 194, 147, 164, 211, 148, 26, 147, 184, 61, 91, 214, 178, 89, 51, 52, 126, 70, 221, 227, 50, 86, 0, 0, 0, 0]
success!!!
[236, 223, 30, 28, 59, 174, 47, 155, 227, 255, 92, 167, 52, 114, 229, 168, 243, 109, 146, 148, 1

In [14]:
#test param i < 4(for循环执行4次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 374
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(374,375)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate4 = success_num / 1000
print('when for execute 4 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 374
repeat      = 1
output      = clock_xor

success!!!
[132, 111, 139, 164, 143, 111, 155, 238, 74, 118, 156, 108, 107, 106, 142, 37, 97, 152, 199, 220, 169, 32, 214, 6, 113, 109, 236, 103, 49, 188, 32, 104, 149, 96, 18, 119, 4, 186, 68, 70, 36, 130, 1, 131, 0, 0, 0, 0]
success!!!
[132, 111, 139, 164, 143, 111, 155, 238, 74, 118, 156, 108, 107, 106, 142, 37, 97, 152, 199, 220, 169, 32, 214, 6, 113, 109, 236, 103, 49, 188, 32, 104, 149, 96, 18, 119, 4, 186, 68, 70, 36, 130, 1, 131, 0, 0, 0, 0]
success!!!
[132, 111, 139, 164, 143, 111, 155, 238, 74, 118, 156, 108, 107, 106, 142, 37, 97, 152, 199, 220, 169, 32, 214, 6, 113, 109, 236, 103, 49, 188, 32, 104, 149, 96, 18, 119, 4, 186, 68, 70, 36, 130, 1, 131, 0, 0, 0, 0]
success!!!
[132, 111, 139, 164, 143, 111, 155, 238, 74, 118, 156, 108, 107, 106, 142, 37, 97, 152, 199, 220, 1

In [15]:
#test param i < 5(for循环执行5次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 401
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(401,402)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate5 = success_num / 1000
print('when for execute 5 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 401
repeat      = 1
output      = clock_xor

success!!!
[219, 73, 236, 225, 226, 47, 59, 98, 220, 154, 70, 139, 40, 38, 240, 239, 187, 118, 23, 159, 61, 100, 46, 100, 57, 96, 2, 40, 128, 170, 61, 162, 50, 228, 35, 142, 183, 40, 196, 176, 97, 215, 247, 114, 0, 0, 0, 0]
success!!!
[219, 73, 236, 225, 226, 47, 59, 98, 220, 154, 70, 139, 40, 38, 240, 239, 187, 118, 23, 159, 61, 100, 46, 100, 57, 96, 2, 40, 128, 170, 61, 162, 50, 228, 35, 142, 183, 40, 196, 176, 97, 215, 247, 114, 0, 0, 0, 0]
success!!!
[219, 73, 236, 225, 226, 47, 59, 98, 220, 154, 70, 139, 40, 38, 240, 239, 187, 118, 23, 159, 61, 100, 46, 100, 57, 96, 2, 40, 128, 170, 61, 162, 50, 228, 35, 142, 183, 40, 196, 176, 97, 215, 247, 114, 0, 0, 0, 0]
success!!!
[219, 73, 236, 225, 226, 47, 59, 98, 220, 154, 70, 139, 40, 38, 240, 239, 187, 118, 23, 159, 61, 100, 46, 10

In [16]:
#test param i < 6(for循环执行6次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 428
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(428,429)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate6 = success_num / 1000
print('when for execute 6 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 428
repeat      = 1
output      = clock_xor

success!!!
[15, 180, 208, 232, 145, 71, 7, 58, 208, 153, 184, 7, 213, 57, 24, 78, 200, 36, 2, 98, 10, 68, 139, 28, 248, 250, 114, 199, 158, 94, 118, 9, 72, 13, 187, 99, 30, 191, 149, 126, 156, 134, 118, 74, 0, 0, 0, 0]
success!!!
[15, 180, 208, 232, 145, 71, 7, 58, 208, 153, 184, 7, 213, 57, 24, 78, 200, 36, 2, 98, 10, 68, 139, 28, 248, 250, 114, 199, 158, 94, 118, 9, 72, 13, 187, 99, 30, 191, 149, 126, 156, 134, 118, 74, 0, 0, 0, 0]
success!!!
[15, 180, 208, 232, 145, 71, 7, 58, 208, 153, 184, 7, 213, 57, 24, 78, 200, 36, 2, 98, 10, 68, 139, 28, 248, 250, 114, 199, 158, 94, 118, 9, 72, 13, 187, 99, 30, 191, 149, 126, 156, 134, 118, 74, 0, 0, 0, 0]
success!!!
[15, 180, 208, 232, 145, 71, 7, 58, 208, 153, 184, 7, 213, 57, 24, 78, 200, 36, 2, 98, 10, 68, 139, 28, 248, 250, 114, 199,

In [17]:
#test param i < 7(for循环执行7次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 455
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(455,456)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate7 = success_num / 1000
print('when for execute 7 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 455
repeat      = 1
output      = clock_xor

success!!!
[213, 242, 25, 12, 177, 167, 218, 81, 133, 88, 71, 179, 189, 180, 62, 63, 151, 108, 202, 31, 161, 246, 198, 56, 166, 107, 81, 241, 198, 23, 141, 124, 30, 171, 207, 172, 53, 17, 27, 229, 60, 3, 52, 249, 0, 0, 0, 0]
success!!!
[213, 242, 25, 12, 177, 167, 218, 81, 133, 88, 71, 179, 189, 180, 62, 63, 151, 108, 202, 31, 161, 246, 198, 56, 166, 107, 81, 241, 198, 23, 141, 124, 30, 171, 207, 172, 53, 17, 27, 229, 60, 3, 52, 249, 0, 0, 0, 0]
success!!!
[213, 242, 25, 12, 177, 167, 218, 81, 133, 88, 71, 179, 189, 180, 62, 63, 151, 108, 202, 31, 161, 246, 198, 56, 166, 107, 81, 241, 198, 23, 141, 124, 30, 171, 207, 172, 53, 17, 27, 229, 60, 3, 52, 249, 0, 0, 0, 0]
success!!!
[213, 242, 25, 12, 177, 167, 218, 81, 133, 88, 71, 179, 189, 180, 62, 63, 151, 108, 202, 31, 161, 246, 19

In [18]:
#test param i < 8(for循环执行8次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 482
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(482,483)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate8 = success_num / 1000
print('when for execute 8 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 482
repeat      = 1
output      = clock_xor

success!!!
[169, 113, 171, 29, 174, 97, 134, 133, 65, 120, 119, 173, 148, 192, 77, 184, 112, 128, 147, 146, 195, 90, 133, 251, 242, 224, 168, 178, 232, 21, 178, 131, 159, 80, 193, 8, 203, 226, 107, 120, 240, 31, 206, 139, 0, 0, 0, 0]
success!!!
[169, 113, 171, 29, 174, 97, 134, 133, 65, 120, 119, 173, 148, 192, 77, 184, 112, 128, 147, 146, 195, 90, 133, 251, 242, 224, 168, 178, 232, 21, 178, 131, 159, 80, 193, 8, 203, 226, 107, 120, 240, 31, 206, 139, 0, 0, 0, 0]
success!!!
[169, 113, 171, 29, 174, 97, 134, 133, 65, 120, 119, 173, 148, 192, 77, 184, 112, 128, 147, 146, 195, 90, 133, 251, 242, 224, 168, 178, 232, 21, 178, 131, 159, 80, 193, 8, 203, 226, 107, 120, 240, 31, 206, 139, 0, 0, 0, 0]
success!!!
[169, 113, 171, 29, 174, 97, 134, 133, 65, 120, 119, 173, 148, 192, 77, 184, 1

In [19]:
#test param i < 9(for循环执行9次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 509
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(509,510)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate9 = success_num / 1000
print('when for execute 9 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 509
repeat      = 1
output      = clock_xor

success!!!
[129, 212, 47, 3, 50, 229, 49, 4, 180, 142, 1, 58, 61, 41, 180, 91, 73, 121, 32, 125, 12, 46, 85, 178, 158, 211, 130, 169, 43, 30, 211, 249, 62, 191, 59, 186, 182, 189, 76, 154, 148, 201, 7, 38, 0, 0, 0, 0]
success!!!
[129, 212, 47, 3, 50, 229, 49, 4, 180, 142, 1, 58, 61, 41, 180, 91, 73, 121, 32, 125, 12, 46, 85, 178, 158, 211, 130, 169, 43, 30, 211, 249, 62, 191, 59, 186, 182, 189, 76, 154, 148, 201, 7, 38, 0, 0, 0, 0]
success!!!
[129, 212, 47, 3, 50, 229, 49, 4, 180, 142, 1, 58, 61, 41, 180, 91, 73, 121, 32, 125, 12, 46, 85, 178, 158, 211, 130, 169, 43, 30, 211, 249, 62, 191, 59, 186, 182, 189, 76, 154, 148, 201, 7, 38, 0, 0, 0, 0]
success!!!
[129, 212, 47, 3, 50, 229, 49, 4, 180, 142, 1, 58, 61, 41, 180, 91, 73, 121, 32, 125, 12, 46, 85, 178, 158, 211, 130, 169, 43,

In [20]:
#test param i < 10(for循环执行10次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 536
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(536,537)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate10 = success_num / 1000
print('when for execute 10 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 536
repeat      = 1
output      = clock_xor

success!!!
[15, 119, 95, 5, 89, 204, 149, 18, 226, 99, 26, 204, 188, 17, 231, 79, 181, 0, 232, 134, 104, 92, 131, 84, 164, 87, 117, 138, 98, 155, 249, 70, 45, 4, 99, 241, 69, 143, 215, 85, 245, 125, 91, 179, 0, 0, 0, 0]
success!!!
[15, 119, 95, 5, 89, 204, 149, 18, 226, 99, 26, 204, 188, 17, 231, 79, 181, 0, 232, 134, 104, 92, 131, 84, 164, 87, 117, 138, 98, 155, 249, 70, 45, 4, 99, 241, 69, 143, 215, 85, 245, 125, 91, 179, 0, 0, 0, 0]
success!!!
[15, 119, 95, 5, 89, 204, 149, 18, 226, 99, 26, 204, 188, 17, 231, 79, 181, 0, 232, 134, 104, 92, 131, 84, 164, 87, 117, 138, 98, 155, 249, 70, 45, 4, 99, 241, 69, 143, 215, 85, 245, 125, 91, 179, 0, 0, 0, 0]
success!!!
[15, 119, 95, 5, 89, 204, 149, 18, 226, 99, 26, 204, 188, 17, 231, 79, 181, 0, 232, 134, 104, 92, 131, 84, 164, 87, 117,

In [21]:
#test param i < 11(for循环执行11次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 563
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(563,564)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate11 = success_num / 1000
print('when for execute 11 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 563
repeat      = 1
output      = clock_xor

success!!!
[250, 199, 148, 130, 124, 113, 83, 28, 149, 107, 41, 81, 128, 189, 147, 88, 157, 205, 123, 117, 163, 28, 39, 52, 232, 207, 39, 155, 11, 199, 63, 51, 123, 62, 47, 5, 31, 28, 152, 9, 216, 117, 174, 101, 0, 0, 0, 0]
success!!!
[250, 199, 148, 130, 124, 113, 83, 28, 149, 107, 41, 81, 128, 189, 147, 88, 157, 205, 123, 117, 163, 28, 39, 52, 232, 207, 39, 155, 11, 199, 63, 51, 123, 62, 47, 5, 31, 28, 152, 9, 216, 117, 174, 101, 0, 0, 0, 0]
success!!!
[250, 199, 148, 130, 124, 113, 83, 28, 149, 107, 41, 81, 128, 189, 147, 88, 157, 205, 123, 117, 163, 28, 39, 52, 232, 207, 39, 155, 11, 199, 63, 51, 123, 62, 47, 5, 31, 28, 152, 9, 216, 117, 174, 101, 0, 0, 0, 0]
success!!!
[250, 199, 148, 130, 124, 113, 83, 28, 149, 107, 41, 81, 128, 189, 147, 88, 157, 205, 123, 117, 163, 28, 39,

In [22]:
#test param i < 12(for循环执行12次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 590
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(590,591)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate12 = success_num / 1000
print('when for execute 12 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 590
repeat      = 1
output      = clock_xor

success!!!
[156, 134, 51, 137, 102, 50, 191, 167, 68, 17, 6, 45, 173, 164, 203, 221, 170, 144, 51, 227, 161, 101, 225, 56, 186, 72, 164, 227, 101, 83, 206, 63, 212, 112, 182, 107, 198, 8, 163, 138, 243, 249, 124, 126, 0, 0, 0, 0]
success!!!
[156, 134, 51, 137, 102, 50, 191, 167, 68, 17, 6, 45, 173, 164, 203, 221, 170, 144, 51, 227, 161, 101, 225, 56, 186, 72, 164, 227, 101, 83, 206, 63, 212, 112, 182, 107, 198, 8, 163, 138, 243, 249, 124, 126, 0, 0, 0, 0]
success!!!
[156, 134, 51, 137, 102, 50, 191, 167, 68, 17, 6, 45, 173, 164, 203, 221, 170, 144, 51, 227, 161, 101, 225, 56, 186, 72, 164, 227, 101, 83, 206, 63, 212, 112, 182, 107, 198, 8, 163, 138, 243, 249, 124, 126, 0, 0, 0, 0]
success!!!
[156, 134, 51, 137, 102, 50, 191, 167, 68, 17, 6, 45, 173, 164, 203, 221, 170, 144, 51, 22

In [23]:
#test param i < 13(for循环执行13次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 617
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(617,618)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate13 = success_num / 1000
print('when for execute 13 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 617
repeat      = 1
output      = clock_xor

success!!!
[71, 235, 134, 248, 5, 77, 76, 255, 245, 128, 230, 215, 116, 186, 225, 199, 45, 9, 125, 202, 117, 205, 30, 157, 134, 217, 50, 67, 204, 235, 127, 129, 196, 203, 40, 119, 28, 219, 116, 92, 88, 120, 191, 190, 0, 0, 0, 0]
success!!!
[71, 235, 134, 248, 5, 77, 76, 255, 245, 128, 230, 215, 116, 186, 225, 199, 45, 9, 125, 202, 117, 205, 30, 157, 134, 217, 50, 67, 204, 235, 127, 129, 196, 203, 40, 119, 28, 219, 116, 92, 88, 120, 191, 190, 0, 0, 0, 0]
success!!!
[71, 235, 134, 248, 5, 77, 76, 255, 245, 128, 230, 215, 116, 186, 225, 199, 45, 9, 125, 202, 117, 205, 30, 157, 134, 217, 50, 67, 204, 235, 127, 129, 196, 203, 40, 119, 28, 219, 116, 92, 88, 120, 191, 190, 0, 0, 0, 0]
success!!!
[71, 235, 134, 248, 5, 77, 76, 255, 245, 128, 230, 215, 116, 186, 225, 199, 45, 9, 125, 202, 

In [24]:
#test param i < 14(for循环执行14次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 644
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(644,645)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate14 = success_num / 1000
print('when for execute 14 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 644
repeat      = 1
output      = clock_xor

success!!!
[136, 22, 180, 173, 66, 121, 132, 76, 171, 249, 156, 24, 1, 234, 182, 150, 176, 69, 197, 206, 138, 156, 92, 20, 26, 217, 216, 51, 72, 80, 66, 226, 221, 69, 91, 21, 93, 101, 76, 85, 227, 53, 32, 214, 0, 0, 0, 0]
success!!!
[136, 22, 180, 173, 66, 121, 132, 76, 171, 249, 156, 24, 1, 234, 182, 150, 176, 69, 197, 206, 138, 156, 92, 20, 26, 217, 216, 51, 72, 80, 66, 226, 221, 69, 91, 21, 93, 101, 76, 85, 227, 53, 32, 214, 0, 0, 0, 0]
success!!!
[136, 22, 180, 173, 66, 121, 132, 76, 171, 249, 156, 24, 1, 234, 182, 150, 176, 69, 197, 206, 138, 156, 92, 20, 26, 217, 216, 51, 72, 80, 66, 226, 221, 69, 91, 21, 93, 101, 76, 85, 227, 53, 32, 214, 0, 0, 0, 0]
success!!!
[136, 22, 180, 173, 66, 121, 132, 76, 171, 249, 156, 24, 1, 234, 182, 150, 176, 69, 197, 206, 138, 156, 92, 20, 26

In [25]:
#test param i < 15(for循环执行15次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 671
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(671,672)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate15 = success_num / 1000
print('when for execute 15 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 671
repeat      = 1
output      = clock_xor

success!!!
[160, 132, 250, 57, 138, 80, 124, 29, 195, 18, 37, 148, 167, 31, 118, 106, 9, 142, 193, 6, 126, 62, 81, 192, 63, 20, 95, 188, 162, 1, 201, 160, 5, 64, 175, 40, 173, 213, 245, 105, 40, 207, 104, 76, 0, 0, 0, 0]
success!!!
[160, 132, 250, 57, 138, 80, 124, 29, 195, 18, 37, 148, 167, 31, 118, 106, 9, 142, 193, 6, 126, 62, 81, 192, 63, 20, 95, 188, 162, 1, 201, 160, 5, 64, 175, 40, 173, 213, 245, 105, 40, 207, 104, 76, 0, 0, 0, 0]
success!!!
[160, 132, 250, 57, 138, 80, 124, 29, 195, 18, 37, 148, 167, 31, 118, 106, 9, 142, 193, 6, 126, 62, 81, 192, 63, 20, 95, 188, 162, 1, 201, 160, 5, 64, 175, 40, 173, 213, 245, 105, 40, 207, 104, 76, 0, 0, 0, 0]
success!!!
[160, 132, 250, 57, 138, 80, 124, 29, 195, 18, 37, 148, 167, 31, 118, 106, 9, 142, 193, 6, 126, 62, 81, 192, 63, 20, 

In [26]:
#test param i < 16(for循环执行16次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 698
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(698,699)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate16 = success_num / 1000
print('when for execute 16 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 698
repeat      = 1
output      = clock_xor

success!!!
[134, 41, 60, 198, 34, 215, 182, 109, 144, 40, 219, 62, 254, 210, 168, 193, 94, 134, 69, 88, 95, 248, 239, 221, 35, 133, 87, 40, 56, 70, 162, 26, 136, 227, 159, 191, 56, 125, 18, 109, 57, 122, 29, 193, 0, 0, 0, 0]
success!!!
[134, 41, 60, 198, 34, 215, 182, 109, 144, 40, 219, 62, 254, 210, 168, 193, 94, 134, 69, 88, 95, 248, 239, 221, 35, 133, 87, 40, 56, 70, 162, 26, 136, 227, 159, 191, 56, 125, 18, 109, 57, 122, 29, 193, 0, 0, 0, 0]
success!!!
[134, 41, 60, 198, 34, 215, 182, 109, 144, 40, 219, 62, 254, 210, 168, 193, 94, 134, 69, 88, 95, 248, 239, 221, 35, 133, 87, 40, 56, 70, 162, 26, 136, 227, 159, 191, 56, 125, 18, 109, 57, 122, 29, 193, 0, 0, 0, 0]
success!!!
[134, 41, 60, 198, 34, 215, 182, 109, 144, 40, 219, 62, 254, 210, 168, 193, 94, 134, 69, 88, 95, 248, 239

In [27]:
#test param i < 17(for循环执行17次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 725
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(725,726)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate17 = success_num / 1000
print('when for execute 17 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 725
repeat      = 1
output      = clock_xor

success!!!
[244, 108, 53, 139, 106, 187, 49, 149, 117, 215, 212, 46, 47, 171, 114, 203, 250, 30, 11, 104, 242, 125, 238, 13, 3, 123, 30, 12, 37, 32, 23, 137, 24, 210, 206, 26, 161, 1, 8, 140, 183, 32, 245, 240, 0, 0, 0, 0]
success!!!
[244, 108, 53, 139, 106, 187, 49, 149, 117, 215, 212, 46, 47, 171, 114, 203, 250, 30, 11, 104, 242, 125, 238, 13, 3, 123, 30, 12, 37, 32, 23, 137, 24, 210, 206, 26, 161, 1, 8, 140, 183, 32, 245, 240, 0, 0, 0, 0]
success!!!
[244, 108, 53, 139, 106, 187, 49, 149, 117, 215, 212, 46, 47, 171, 114, 203, 250, 30, 11, 104, 242, 125, 238, 13, 3, 123, 30, 12, 37, 32, 23, 137, 24, 210, 206, 26, 161, 1, 8, 140, 183, 32, 245, 240, 0, 0, 0, 0]
success!!!
[244, 108, 53, 139, 106, 187, 49, 149, 117, 215, 212, 46, 47, 171, 114, 203, 250, 30, 11, 104, 242, 125, 238, 1

In [28]:
#test param i < 18(for循环执行18次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 752
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(752,753)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate18 = success_num / 1000
print('when for execute 18 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 752
repeat      = 1
output      = clock_xor

success!!!
[80, 115, 188, 198, 5, 70, 183, 115, 19, 90, 27, 63, 72, 203, 92, 223, 249, 2, 70, 93, 90, 140, 29, 145, 207, 45, 165, 190, 177, 68, 193, 191, 181, 154, 76, 242, 9, 108, 143, 208, 189, 56, 247, 255, 0, 0, 0, 0]
success!!!
[80, 115, 188, 198, 5, 70, 183, 115, 19, 90, 27, 63, 72, 203, 92, 223, 249, 2, 70, 93, 90, 140, 29, 145, 207, 45, 165, 190, 177, 68, 193, 191, 181, 154, 76, 242, 9, 108, 143, 208, 189, 56, 247, 255, 0, 0, 0, 0]
success!!!
[80, 115, 188, 198, 5, 70, 183, 115, 19, 90, 27, 63, 72, 203, 92, 223, 249, 2, 70, 93, 90, 140, 29, 145, 207, 45, 165, 190, 177, 68, 193, 191, 181, 154, 76, 242, 9, 108, 143, 208, 189, 56, 247, 255, 0, 0, 0, 0]
success!!!
[80, 115, 188, 198, 5, 70, 183, 115, 19, 90, 27, 63, 72, 203, 92, 223, 249, 2, 70, 93, 90, 140, 29, 145, 207, 45, 

In [29]:
#test param i < 19(for循环执行19次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 779
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(779,780)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate19 = success_num / 1000
print('when for execute 19 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 779
repeat      = 1
output      = clock_xor

success!!!
[95, 241, 222, 43, 40, 130, 159, 125, 149, 167, 51, 28, 62, 202, 79, 140, 214, 55, 170, 108, 18, 219, 168, 108, 174, 151, 0, 181, 2, 21, 64, 90, 237, 5, 239, 55, 85, 10, 4, 46, 74, 132, 211, 236, 0, 0, 0, 0]
success!!!
[95, 241, 222, 43, 40, 130, 159, 125, 149, 167, 51, 28, 62, 202, 79, 140, 214, 55, 170, 108, 18, 219, 168, 108, 174, 151, 0, 181, 2, 21, 64, 90, 237, 5, 239, 55, 85, 10, 4, 46, 74, 132, 211, 236, 0, 0, 0, 0]
success!!!
[95, 241, 222, 43, 40, 130, 159, 125, 149, 167, 51, 28, 62, 202, 79, 140, 214, 55, 170, 108, 18, 219, 168, 108, 174, 151, 0, 181, 2, 21, 64, 90, 237, 5, 239, 55, 85, 10, 4, 46, 74, 132, 211, 236, 0, 0, 0, 0]
success!!!
[95, 241, 222, 43, 40, 130, 159, 125, 149, 167, 51, 28, 62, 202, 79, 140, 214, 55, 170, 108, 18, 219, 168, 108, 174, 151, 0

In [30]:
#test param i < 20(for循环执行20次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 806
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(806,807)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate20 = success_num / 1000
print('when for execute 20 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 806
repeat      = 1
output      = clock_xor

success!!!
[7, 67, 154, 200, 59, 186, 229, 253, 138, 121, 107, 77, 82, 8, 41, 250, 133, 100, 86, 139, 99, 61, 93, 133, 235, 17, 117, 238, 26, 20, 8, 82, 50, 62, 236, 57, 91, 39, 169, 248, 243, 109, 152, 248, 0, 0, 0, 0]
success!!!
[7, 67, 154, 200, 59, 186, 229, 253, 138, 121, 107, 77, 82, 8, 41, 250, 133, 100, 86, 139, 99, 61, 93, 133, 235, 17, 117, 238, 26, 20, 8, 82, 50, 62, 236, 57, 91, 39, 169, 248, 243, 109, 152, 248, 0, 0, 0, 0]
success!!!
[7, 67, 154, 200, 59, 186, 229, 253, 138, 121, 107, 77, 82, 8, 41, 250, 133, 100, 86, 139, 99, 61, 93, 133, 235, 17, 117, 238, 26, 20, 8, 82, 50, 62, 236, 57, 91, 39, 169, 248, 243, 109, 152, 248, 0, 0, 0, 0]
success!!!
[7, 67, 154, 200, 59, 186, 229, 253, 138, 121, 107, 77, 82, 8, 41, 250, 133, 100, 86, 139, 99, 61, 93, 133, 235, 17, 117

In [31]:
#test param i < 21(for循环执行21次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 833
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(833,834)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate21 = success_num / 1000
print('when for execute 21 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 833
repeat      = 1
output      = clock_xor

success!!!
[242, 137, 18, 174, 214, 124, 19, 183, 211, 2, 238, 108, 136, 3, 167, 247, 246, 58, 152, 251, 221, 82, 193, 61, 245, 198, 124, 216, 226, 165, 132, 47, 151, 5, 254, 109, 141, 78, 17, 251, 170, 68, 84, 157, 0, 0, 0, 0]
success!!!
[242, 137, 18, 174, 214, 124, 19, 183, 211, 2, 238, 108, 136, 3, 167, 247, 246, 58, 152, 251, 221, 82, 193, 61, 245, 198, 124, 216, 226, 165, 132, 47, 151, 5, 254, 109, 141, 78, 17, 251, 170, 68, 84, 157, 0, 0, 0, 0]
success!!!
[242, 137, 18, 174, 214, 124, 19, 183, 211, 2, 238, 108, 136, 3, 167, 247, 246, 58, 152, 251, 221, 82, 193, 61, 245, 198, 124, 216, 226, 165, 132, 47, 151, 5, 254, 109, 141, 78, 17, 251, 170, 68, 84, 157, 0, 0, 0, 0]
success!!!
[242, 137, 18, 174, 214, 124, 19, 183, 211, 2, 238, 108, 136, 3, 167, 247, 246, 58, 152, 251, 22

In [32]:
#test param i < 22(for循环执行22次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 860
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(860,861)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate22 = success_num / 1000
print('when for execute 22 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 860
repeat      = 1
output      = clock_xor

success!!!
[81, 219, 2, 129, 227, 208, 184, 99, 84, 247, 169, 114, 46, 151, 214, 96, 217, 46, 149, 186, 97, 193, 71, 14, 79, 151, 167, 189, 239, 121, 61, 253, 238, 215, 57, 35, 183, 129, 71, 255, 248, 202, 235, 17, 0, 0, 0, 0]
success!!!
[81, 219, 2, 129, 227, 208, 184, 99, 84, 247, 169, 114, 46, 151, 214, 96, 217, 46, 149, 186, 97, 193, 71, 14, 79, 151, 167, 189, 239, 121, 61, 253, 238, 215, 57, 35, 183, 129, 71, 255, 248, 202, 235, 17, 0, 0, 0, 0]
success!!!
[81, 219, 2, 129, 227, 208, 184, 99, 84, 247, 169, 114, 46, 151, 214, 96, 217, 46, 149, 186, 97, 193, 71, 14, 79, 151, 167, 189, 239, 121, 61, 253, 238, 215, 57, 35, 183, 129, 71, 255, 248, 202, 235, 17, 0, 0, 0, 0]
success!!!
[81, 219, 2, 129, 227, 208, 184, 99, 84, 247, 169, 114, 46, 151, 214, 96, 217, 46, 149, 186, 97, 19

In [33]:
#test param i < 23(for循环执行23次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 887
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(887,888)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate23 = success_num / 1000
print('when for execute 23 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 887
repeat      = 1
output      = clock_xor

success!!!
[83, 153, 148, 86, 84, 17, 146, 35, 195, 197, 20, 62, 205, 174, 143, 145, 52, 246, 126, 170, 46, 247, 123, 233, 196, 9, 203, 116, 154, 58, 86, 80, 188, 152, 132, 40, 126, 58, 215, 171, 159, 184, 202, 109, 0, 0, 0, 0]
success!!!
[83, 153, 148, 86, 84, 17, 146, 35, 195, 197, 20, 62, 205, 174, 143, 145, 52, 246, 126, 170, 46, 247, 123, 233, 196, 9, 203, 116, 154, 58, 86, 80, 188, 152, 132, 40, 126, 58, 215, 171, 159, 184, 202, 109, 0, 0, 0, 0]
success!!!
[83, 153, 148, 86, 84, 17, 146, 35, 195, 197, 20, 62, 205, 174, 143, 145, 52, 246, 126, 170, 46, 247, 123, 233, 196, 9, 203, 116, 154, 58, 86, 80, 188, 152, 132, 40, 126, 58, 215, 171, 159, 184, 202, 109, 0, 0, 0, 0]
success!!!
[83, 153, 148, 86, 84, 17, 146, 35, 195, 197, 20, 62, 205, 174, 143, 145, 52, 246, 126, 170, 46,

In [34]:
#test param i < 24(for循环执行24次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 914
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(914,915)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate24 = success_num / 1000
print('when for execute 24 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 914
repeat      = 1
output      = clock_xor

success!!!
[118, 72, 219, 201, 147, 181, 171, 78, 177, 25, 69, 97, 131, 249, 75, 210, 47, 44, 161, 170, 67, 161, 52, 34, 148, 24, 121, 86, 171, 65, 105, 28, 96, 217, 244, 220, 162, 45, 94, 127, 38, 252, 20, 42, 0, 0, 0, 0]
success!!!
[118, 72, 219, 201, 147, 181, 171, 78, 177, 25, 69, 97, 131, 249, 75, 210, 47, 44, 161, 170, 67, 161, 52, 34, 148, 24, 121, 86, 171, 65, 105, 28, 96, 217, 244, 220, 162, 45, 94, 127, 38, 252, 20, 42, 0, 0, 0, 0]
success!!!
[118, 72, 219, 201, 147, 181, 171, 78, 177, 25, 69, 97, 131, 249, 75, 210, 47, 44, 161, 170, 67, 161, 52, 34, 148, 24, 121, 86, 171, 65, 105, 28, 96, 217, 244, 220, 162, 45, 94, 127, 38, 252, 20, 42, 0, 0, 0, 0]
success!!!
[118, 72, 219, 201, 147, 181, 171, 78, 177, 25, 69, 97, 131, 249, 75, 210, 47, 44, 161, 170, 67, 161, 52, 34, 1

In [35]:
#test param i < 25(for循环执行25次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 941
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(941,942)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate25 = success_num / 1000
print('when for execute 25 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 941
repeat      = 1
output      = clock_xor

success!!!
[16, 133, 226, 124, 114, 116, 76, 203, 134, 105, 247, 236, 219, 166, 14, 175, 144, 67, 154, 52, 179, 229, 67, 219, 171, 8, 228, 191, 95, 125, 197, 140, 246, 174, 228, 94, 125, 111, 44, 26, 187, 173, 14, 86, 0, 0, 0, 0]
success!!!
[16, 133, 226, 124, 114, 116, 76, 203, 134, 105, 247, 236, 219, 166, 14, 175, 144, 67, 154, 52, 179, 229, 67, 219, 171, 8, 228, 191, 95, 125, 197, 140, 246, 174, 228, 94, 125, 111, 44, 26, 187, 173, 14, 86, 0, 0, 0, 0]
success!!!
[16, 133, 226, 124, 114, 116, 76, 203, 134, 105, 247, 236, 219, 166, 14, 175, 144, 67, 154, 52, 179, 229, 67, 219, 171, 8, 228, 191, 95, 125, 197, 140, 246, 174, 228, 94, 125, 111, 44, 26, 187, 173, 14, 86, 0, 0, 0, 0]
success!!!
[16, 133, 226, 124, 114, 116, 76, 203, 134, 105, 247, 236, 219, 166, 14, 175, 144, 67, 154

In [36]:
#test param i < 26(for循环执行26次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 968
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(968,969)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate26 = success_num / 1000
print('when for execute 26 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 968
repeat      = 1
output      = clock_xor

success!!!
[161, 231, 115, 174, 109, 174, 243, 51, 252, 155, 152, 83, 212, 9, 207, 86, 247, 242, 129, 35, 60, 38, 174, 22, 248, 233, 83, 90, 202, 131, 253, 42, 182, 14, 220, 21, 102, 0, 227, 215, 107, 119, 25, 56, 0, 0, 0, 0]
success!!!
[161, 231, 115, 174, 109, 174, 243, 51, 252, 155, 152, 83, 212, 9, 207, 86, 247, 242, 129, 35, 60, 38, 174, 22, 248, 233, 83, 90, 202, 131, 253, 42, 182, 14, 220, 21, 102, 0, 227, 215, 107, 119, 25, 56, 0, 0, 0, 0]
success!!!
[161, 231, 115, 174, 109, 174, 243, 51, 252, 155, 152, 83, 212, 9, 207, 86, 247, 242, 129, 35, 60, 38, 174, 22, 248, 233, 83, 90, 202, 131, 253, 42, 182, 14, 220, 21, 102, 0, 227, 215, 107, 119, 25, 56, 0, 0, 0, 0]
success!!!
[161, 231, 115, 174, 109, 174, 243, 51, 252, 155, 152, 83, 212, 9, 207, 86, 247, 242, 129, 35, 60, 38,

In [37]:
#test param i < 27(for循环执行27次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset =995
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(995,996)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate27 = success_num / 1000
print('when for execute 27 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 995
repeat      = 1
output      = clock_xor

success!!!
[225, 78, 37, 128, 241, 38, 200, 246, 203, 57, 63, 189, 60, 244, 242, 53, 117, 219, 13, 175, 207, 73, 11, 166, 238, 81, 244, 172, 89, 10, 80, 65, 139, 247, 155, 19, 118, 66, 33, 71, 130, 207, 125, 118, 0, 0, 0, 0]
success!!!
[225, 78, 37, 128, 241, 38, 200, 246, 203, 57, 63, 189, 60, 244, 242, 53, 117, 219, 13, 175, 207, 73, 11, 166, 238, 81, 244, 172, 89, 10, 80, 65, 139, 247, 155, 19, 118, 66, 33, 71, 130, 207, 125, 118, 0, 0, 0, 0]
success!!!
[225, 78, 37, 128, 241, 38, 200, 246, 203, 57, 63, 189, 60, 244, 242, 53, 117, 219, 13, 175, 207, 73, 11, 166, 238, 81, 244, 172, 89, 10, 80, 65, 139, 247, 155, 19, 118, 66, 33, 71, 130, 207, 125, 118, 0, 0, 0, 0]
success!!!
[225, 78, 37, 128, 241, 38, 200, 246, 203, 57, 63, 189, 60, 244, 242, 53, 117, 219, 13, 175, 207, 73, 11,

In [38]:
#test param i < 28(for循环执行28次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 1022
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(1022,1023)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate28 = success_num / 1000
print('when for execute 28 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 1022
repeat      = 1
output      = clock_xor

success!!!
[205, 77, 86, 3, 132, 190, 67, 23, 200, 70, 181, 129, 26, 100, 69, 42, 35, 193, 36, 96, 215, 145, 62, 140, 153, 58, 205, 140, 172, 19, 244, 240, 172, 34, 176, 150, 30, 205, 223, 102, 255, 155, 164, 112, 0, 0, 0, 0]
success!!!
[205, 77, 86, 3, 132, 190, 67, 23, 200, 70, 181, 129, 26, 100, 69, 42, 35, 193, 36, 96, 215, 145, 62, 140, 153, 58, 205, 140, 172, 19, 244, 240, 172, 34, 176, 150, 30, 205, 223, 102, 255, 155, 164, 112, 0, 0, 0, 0]
success!!!
[205, 77, 86, 3, 132, 190, 67, 23, 200, 70, 181, 129, 26, 100, 69, 42, 35, 193, 36, 96, 215, 145, 62, 140, 153, 58, 205, 140, 172, 19, 244, 240, 172, 34, 176, 150, 30, 205, 223, 102, 255, 155, 164, 112, 0, 0, 0, 0]
success!!!
[205, 77, 86, 3, 132, 190, 67, 23, 200, 70, 181, 129, 26, 100, 69, 42, 35, 193, 36, 96, 215, 145, 62,

In [39]:
#test param i < 29(for循环执行29次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 1049
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(1049,1050)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate29 = success_num / 1000
print('when for execute 29 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 1049
repeat      = 1
output      = clock_xor

success!!!
[96, 146, 102, 160, 165, 44, 171, 21, 86, 177, 58, 67, 86, 36, 228, 97, 167, 10, 49, 186, 174, 113, 102, 116, 88, 251, 72, 231, 30, 25, 41, 62, 223, 221, 178, 88, 180, 237, 63, 108, 117, 202, 197, 208, 0, 0, 0, 0]
success!!!
[96, 146, 102, 160, 165, 44, 171, 21, 86, 177, 58, 67, 86, 36, 228, 97, 167, 10, 49, 186, 174, 113, 102, 116, 88, 251, 72, 231, 30, 25, 41, 62, 223, 221, 178, 88, 180, 237, 63, 108, 117, 202, 197, 208, 0, 0, 0, 0]
success!!!
[96, 146, 102, 160, 165, 44, 171, 21, 86, 177, 58, 67, 86, 36, 228, 97, 167, 10, 49, 186, 174, 113, 102, 116, 88, 251, 72, 231, 30, 25, 41, 62, 223, 221, 178, 88, 180, 237, 63, 108, 117, 202, 197, 208, 0, 0, 0, 0]
success!!!
[96, 146, 102, 160, 165, 44, 171, 21, 86, 177, 58, 67, 86, 36, 228, 97, 167, 10, 49, 186, 174, 113, 102,

In [40]:
#test param i < 30(for循环执行30次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 1076
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(1076,1077)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate30 = success_num / 1000
print('when for execute 30 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 1076
repeat      = 1
output      = clock_xor

success!!!
[172, 225, 102, 173, 218, 240, 206, 42, 127, 74, 61, 152, 65, 207, 135, 60, 88, 198, 61, 208, 41, 234, 57, 139, 177, 168, 102, 170, 5, 146, 186, 60, 101, 5, 247, 130, 155, 91, 222, 161, 212, 103, 253, 118, 0, 0, 0, 0]
success!!!
[172, 225, 102, 173, 218, 240, 206, 42, 127, 74, 61, 152, 65, 207, 135, 60, 88, 198, 61, 208, 41, 234, 57, 139, 177, 168, 102, 170, 5, 146, 186, 60, 101, 5, 247, 130, 155, 91, 222, 161, 212, 103, 253, 118, 0, 0, 0, 0]
success!!!
[172, 225, 102, 173, 218, 240, 206, 42, 127, 74, 61, 152, 65, 207, 135, 60, 88, 198, 61, 208, 41, 234, 57, 139, 177, 168, 102, 170, 5, 146, 186, 60, 101, 5, 247, 130, 155, 91, 222, 161, 212, 103, 253, 118, 0, 0, 0, 0]
success!!!
[172, 225, 102, 173, 218, 240, 206, 42, 127, 74, 61, 152, 65, 207, 135, 60, 88, 198, 61, 208

In [41]:
#test param i < 31(for循环执行31次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 1103
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(1103,1104)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate31 = success_num / 1000
print('when for execute 31 times ,the success rate is {}'.format(success_num / 1000))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 1103
repeat      = 1
output      = clock_xor

success!!!
[128, 8, 58, 205, 226, 34, 145, 137, 45, 147, 209, 232, 155, 132, 10, 64, 27, 181, 186, 236, 38, 247, 230, 198, 29, 195, 14, 157, 103, 80, 52, 197, 213, 27, 46, 158, 14, 89, 82, 118, 222, 161, 148, 51, 0, 0, 0, 0]
success!!!
[128, 8, 58, 205, 226, 34, 145, 137, 45, 147, 209, 232, 155, 132, 10, 64, 27, 181, 186, 236, 38, 247, 230, 198, 29, 195, 14, 157, 103, 80, 52, 197, 213, 27, 46, 158, 14, 89, 82, 118, 222, 161, 148, 51, 0, 0, 0, 0]
success!!!
[128, 8, 58, 205, 226, 34, 145, 137, 45, 147, 209, 232, 155, 132, 10, 64, 27, 181, 186, 236, 38, 247, 230, 198, 29, 195, 14, 157, 103, 80, 52, 197, 213, 27, 46, 158, 14, 89, 82, 118, 222, 161, 148, 51, 0, 0, 0, 0]
success!!!
[128, 8, 58, 205, 226, 34, 145, 137, 45, 147, 209, 232, 155, 132, 10, 64, 27, 181, 186, 236, 38, 247, 23

In [42]:
#test param i < 32(for循环执行32次)

#设置故障参数
if scope._is_husky:
    scope.glitch.enabled = True
scope.glitch.clk_src = "clkgen"
scope.glitch.output = "clock_xor"
scope.glitch.trigger_src = "ext_single"
scope.glitch.repeat = 1
scope.io.hs2 = "glitch"
scope.glitch.width =  -3.125
scope.glitch.ext_offset = 1130
scope.glitch.offset = -48.828125 
print(scope.glitch)
# glitch_loc = range(1400,1401)
glitch_loc = range(1130,1131)

#test suceess rate
from tqdm.notebook import tqdm, trange
import logging
import numpy as np
ktp = cw.ktp.Basic()
logging.getLogger().setLevel(logging.ERROR)
reboot_flush()
success_num = 0
for num in range(1000): #当前故障参数ext_offset下对20条随机的消息进行攻击
    mess = get_random_message() #随机生一个长度为33字节的消息，并放入列表中（mess_list）
    p = bytearray(mess,encoding='utf-8') #转换input_list为chipwhisperer能接收的数据
    scope.arm()
    target.simpleserial_write('3', p)
    time.sleep(0.5)
    ret = scope.capture()
    if ret:
        reboot_flush() #bad if we accidentally didn't have this work
        time.sleep(0.1)
        print("timed out!")
        continue
    output = target.simpleserial_read_witherrors('r', 180, glitch_timeout = 3)
    if output['valid']:
        p_list = []
        for ii in range(20,68):
            p_list.append(output['payload'][ii])
        if test_suc(p_list):
            success_num += 1    
        reboot_flush()
    else:
        reboot_flush()
success_rate32 = success_num / 1000
print('when for execute 32 times ,the success rate is {}'.format(success_rate32))

(ChipWhisperer Glitch WARNING|File ChipWhispererGlitch.py:942) Negative offsets <-45 may result in double glitches!


clk_src     = clkgen
width       = -3.125
width_fine  = 0
offset      = -48.828125
offset_fine = 0
trigger_src = ext_single
arm_timing  = after_scope
ext_offset  = 1130
repeat      = 1
output      = clock_xor

success!!!
[112, 69, 231, 88, 211, 17, 86, 182, 92, 213, 13, 121, 36, 48, 153, 131, 109, 81, 78, 36, 84, 159, 71, 154, 13, 105, 70, 6, 124, 223, 102, 100, 254, 168, 58, 80, 71, 154, 120, 174, 150, 170, 42, 206, 0, 0, 0, 0]
success!!!
[112, 69, 231, 88, 211, 17, 86, 182, 92, 213, 13, 121, 36, 48, 153, 131, 109, 81, 78, 36, 84, 159, 71, 154, 13, 105, 70, 6, 124, 223, 102, 100, 254, 168, 58, 80, 71, 154, 120, 174, 150, 170, 42, 206, 0, 0, 0, 0]
success!!!
[112, 69, 231, 88, 211, 17, 86, 182, 92, 213, 13, 121, 36, 48, 153, 131, 109, 81, 78, 36, 84, 159, 71, 154, 13, 105, 70, 6, 124, 223, 102, 100, 254, 168, 58, 80, 71, 154, 120, 174, 150, 170, 42, 206, 0, 0, 0, 0]
success!!!
[112, 69, 231, 88, 211, 17, 86, 182, 92, 213, 13, 121, 36, 48, 153, 131, 109, 81, 78, 36, 84, 159, 71, 154, 13

In [43]:
print('when for execute 1 times ,the success rate is {}'.format(success_rate1))
print('when for execute 2 times ,the success rate is {}'.format(success_rate2))
print('when for execute 3 times ,the success rate is {}'.format(success_rate3))
print('when for execute 4 times ,the success rate is {}'.format(success_rate4))
print('when for execute 5 times ,the success rate is {}'.format(success_rate5))
print('when for execute 6 times ,the success rate is {}'.format(success_rate6))
print('when for execute 7 times ,the success rate is {}'.format(success_rate7))
print('when for execute 8 times ,the success rate is {}'.format(success_rate8))
print('when for execute 9 times ,the success rate is {}'.format(success_rate9))
print('when for execute 10 times ,the success rate is {}'.format(success_rate10))
print('when for execute 11 times ,the success rate is {}'.format(success_rate11))
print('when for execute 12 times ,the success rate is {}'.format(success_rate12))
print('when for execute 13 times ,the success rate is {}'.format(success_rate13))
print('when for execute 14 times ,the success rate is {}'.format(success_rate14))
print('when for execute 15 times ,the success rate is {}'.format(success_rate15))
print('when for execute 16 times ,the success rate is {}'.format(success_rate16))
print('when for execute 17 times ,the success rate is {}'.format(success_rate17))
print('when for execute 18 times ,the success rate is {}'.format(success_rate18))
print('when for execute 19 times ,the success rate is {}'.format(success_rate19))
print('when for execute 20 times ,the success rate is {}'.format(success_rate20))
print('when for execute 21 times ,the success rate is {}'.format(success_rate21))
print('when for execute 22 times ,the success rate is {}'.format(success_rate22))
print('when for execute 23 times ,the success rate is {}'.format(success_rate23))
print('when for execute 24 times ,the success rate is {}'.format(success_rate24))
print('when for execute 25 times ,the success rate is {}'.format(success_rate25))
print('when for execute 26 times ,the success rate is {}'.format(success_rate26))
print('when for execute 27 times ,the success rate is {}'.format(success_rate27))
print('when for execute 28 times ,the success rate is {}'.format(success_rate28))
print('when for execute 29 times ,the success rate is {}'.format(success_rate29))
print('when for execute 30 times ,the success rate is {}'.format(success_rate30))
print('when for execute 31 times ,the success rate is {}'.format(success_rate31))
print('when for execute 32 times ,the success rate is {}'.format(success_rate32))

when for execute 1 times ,the success rate is 0.629
when for execute 2 times ,the success rate is 0.568
when for execute 3 times ,the success rate is 0.548
when for execute 4 times ,the success rate is 0.621
when for execute 5 times ,the success rate is 0.624
when for execute 6 times ,the success rate is 0.599
when for execute 7 times ,the success rate is 0.551
when for execute 8 times ,the success rate is 0.56
when for execute 9 times ,the success rate is 0.52
when for execute 10 times ,the success rate is 0.547
when for execute 11 times ,the success rate is 0.632
when for execute 12 times ,the success rate is 0.658
when for execute 13 times ,the success rate is 0.482
when for execute 14 times ,the success rate is 0.636
when for execute 15 times ,the success rate is 0.555
when for execute 16 times ,the success rate is 0.539
when for execute 17 times ,the success rate is 0.508
when for execute 18 times ,the success rate is 0.509
when for execute 19 times ,the success rate is 0.442
when

In [ ]:
scope.dis()
target.dis()